In [1]:
import torch
import torch.nn as nn
torch.cuda.is_available()

True

Check that we can load the tokenizer and the model.  The first time this runs it will take a while.  The files go under ~/.cache/huggingface

In [2]:
from transformers import LlamaTokenizer, LlamaForCausalLM
from peft import prepare_model_for_int8_training
tokenizer = LlamaTokenizer.from_pretrained(
    "decapoda-research/llama-7b-hf")
   
#tokenizer.pad_token_id = (0)
#tokenizer.padding_side = 'left'
model = LlamaForCausalLM.from_pretrained(
    "decapoda-research/llama-7b-hf",
    load_in_8bit=True,
    device_map="auto",
    torch_dtype=torch.float16
)

model = prepare_model_for_int8_training(model)


/home/matt/hf/sqllama-V0/.venv/lib/python3.7/site-packages/bitsandbytes/cuda_setup/main.py:136: UserWarning: /opt/conda did not contain libcudart.so as expected! Searching further paths...
  warn(msg)
The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'LLaMATokenizer'. 
The class this function is called from is 'LlamaTokenizer'.



===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please submit your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
CUDA SETUP: CUDA runtime path found: /usr/local/cuda/lib64/libcudart.so
CUDA SETUP: Highest compute capability among GPUs detected: 7.5
CUDA SETUP: Detected CUDA version 113
CUDA SETUP: Loading binary /home/matt/hf/sqllama-V0/.venv/lib/python3.7/site-packages/bitsandbytes/libbitsandbytes_cuda113.so...


Loading checkpoint shards:   0%|          | 0/33 [00:00<?, ?it/s]

Construct a basic example to interact with the model

In [3]:
def ask(q,l=64):
    toks = tokenizer(q , return_tensors='pt')
    ctoks = toks.input_ids.to('cuda')
    gen = model.generate(ctoks, max_length=64)
    return tokenizer.decode(gen[0])

r = ask('hey dude, talk to me')
print(r)

r = ask('whats the capital of georgia?')
print(r)


/home/matt/hf/sqllama-V0/.venv/lib/python3.7/site-packages/transformers/generation/utils.py:1220: UserWarning: You have modified the pretrained model configuration to control generation. This is a deprecated strategy to control generation and will be removed soon, in a future version. Please use a generation configuration file (see https://huggingface.co/docs/transformers/main_classes/text_generation)
  "You have modified the pretrained model configuration to control generation. This is a"


 ⁇  hey dude, talk to me.
I'm a 20 year old guy from the UK. I'm a bit of a nerd, I like to read, I like to write, I like to play video games, I like to watch movies, I like to listen
 ⁇  whats the capital of georgia?
What is the capital of Georgia?
The capital of Georgia is Atlanta.
What is the capital of Georgia?
The capital of Georgia is Atlanta. The capital of Georgia is Atlanta. The capital of Georgia is Atlanta. The capital of Georgia is Atlanta. The


Get the WikiSQL project so we can get the dataset

In [13]:
! git clone https://github.com/salesforce/WikiSQL
! tar xvjf WikiSQL/data.tar.bz2

fatal: destination path 'WikiSQL' already exists and is not an empty directory.
data/
data/train.jsonl
data/test.tables.jsonl
data/test.db
data/dev.tables.jsonl
data/dev.db
data/test.jsonl
data/train.tables.jsonl
data/train.db
data/dev.jsonl


Figure out what the actual data set has in it.

In [3]:
import json
import sys
import re
sys.path.append('./WikiSQL')
from WikiSQL.lib.query import Query

def replace_cols(qs,cmap):
    for k,v in cmap.items():
        qs = re.sub(f' {k} ',f' {v} ',qs)
    return qs

with open('data/train.jsonl') as f:
    j = f.readline()
    js = json.loads(j)
    print(js)
    
print()

with open('data/train.tables.jsonl') as f:
    j = f.readline()
    js2 = json.loads(j)
    #print(js)
    print(js2['id'])
    print(js2['header'])
    print()
    print(js2)

sql = js['sql']
q = Query.from_dict(sql)
print(q)
cm = {f'col{i}':js2['header'][i] for i in range(len(js2['header']))}
qs = replace_cols(str(q),cm)
print(qs)

{'phase': 1, 'table_id': '1-1000181-1', 'question': 'Tell me what the notes are for South Australia ', 'sql': {'sel': 5, 'conds': [[3, 0, 'SOUTH AUSTRALIA']], 'agg': 0}}

1-1000181-1
['State/territory', 'Text/background colour', 'Format', 'Current slogan', 'Current series', 'Notes']

{'id': '1-1000181-1', 'header': ['State/territory', 'Text/background colour', 'Format', 'Current slogan', 'Current series', 'Notes'], 'types': ['text', 'text', 'text', 'text', 'text', 'text'], 'rows': [['Australian Capital Territory', 'blue/white', 'Yaa·nna', 'ACT · CELEBRATION OF A CENTURY 2013', 'YIL·00A', 'Slogan screenprinted on plate'], ['New South Wales', 'black/yellow', 'aa·nn·aa', 'NEW SOUTH WALES', 'BX·99·HI', 'No slogan on current series'], ['New South Wales', 'black/white', 'aaa·nna', 'NSW', 'CPX·12A', 'Optional white slimline series'], ['Northern Territory', 'ochre/white', 'Ca·nn·aa', 'NT · OUTBACK AUSTRALIA', 'CB·06·ZZ', 'New series began in June 2011'], ['Queensland', 'maroon/white', 'nnn·aaa

Ok, their query class deals poorly with stringifying the constraints.  Let's mock up natural language prompt and SQL response.

In [4]:
import random
import json

# defined by WikiSQL

agg_ops = ['', 'MAX', 'MIN', 'COUNT', 'SUM', 'AVG']
cond_ops = ['=', '>', '<', 'OP']
syms = ['SELECT', 'WHERE', 'AND', 'COL', 'TABLE', 'CAPTION', 'PAGE', 'SECTION', 'OP', 'COND', 'QUESTION', 'AGG', 'AGGOPS', 'CONDOPS']

def fix_repr(d,cols,types,tid):
    sel_index=d['sel'] 
    agg_index=d['agg']
    conditions=d['conds']
    col = cols[sel_index]
    rep = 'SELECT {agg} {sel} FROM {tid}'.format(
            agg=agg_ops[agg_index],
            sel=col,
            tid=tid
            )
    if conditions:
        cs = []
        for i, o, v in conditions:
            #print(i,cols)
            nm = cols[i]
            op = cond_ops[o]
            
            if types[i] in ['text']:
                val = f"\'{v}\'"
            else:
                val = v
            cs.append(f'{nm} {op} {val}')
        #print(cs)

        rep +=  ' WHERE ' + ' AND '.join(cs)
    
    return rep

tbl_cols = {}
tbl_types = {}
tbl_str = {}

prefix = 'Below is a question that describes a data request, paired with an input that describes a SQL table.  Write a SQL query that retrieves the data.'

def tbl_def_to_string(id, header, types):
    ht = [f'{header[i]} ({types[i]})' for i in range(len(header))]
    s = f'\n### Input: Table {id} has columns ' + ','.join(ht) + '.  '
    return s

with open('data/train.tables.jsonl') as f:
    for line in f:
        js = json.loads(line)
        id = js['id']
        hdr = js['header']
        ts = js['types']
        tbl_str[id] = tbl_def_to_string(id,hdr,ts)
        tbl_cols[id] = hdr
        tbl_types[id] = ts


nl_q = []
sql_a = []

with open('data/train.jsonl') as f:
    for line in f:
        js = json.loads(line)
        id = js['table_id']
        s = tbl_str[id]
        qst = js['question']
        nl = prefix + "\n### Question: " + qst + s
        nl_q.append(nl)

        sql = js['sql']
        a = fix_repr(sql,tbl_cols[id],tbl_types[id],id)
        a = '\n### Answer: ' + a
        sql_a.append(a)


M = len(nl_q)

data_txt = [nl_q[i] + sql_a[i] for i in range(len(nl_q))]

for i in range(5):
    j = random.randint(0,M-1)
    print()
    print(data_txt[j]) 
        
   


Below is a question that describes a data request, paired with an input that describes a SQL table.  Write a SQL query that retrieves the data.
### Question: How many games does novica veličković have when there's more than 24 rebounds?
### Input: Table 2-16050349-8 has columns Rank (real),Name (text),Team (text),Games (real),Rebounds (real).  
### Answer: SELECT COUNT Games FROM 2-16050349-8 WHERE Name = 'novica veličković' AND Rebounds > 24

Below is a question that describes a data request, paired with an input that describes a SQL table.  Write a SQL query that retrieves the data.
### Question: What is the number of capacity at somerset park?
### Input: Table 1-11206787-5 has columns Team (text),Stadium (text),Capacity (real),Highest (real),Lowest (real),Average (real).  
### Answer: SELECT COUNT Capacity FROM 1-11206787-5 WHERE Stadium = 'Somerset Park'

Below is a question that describes a data request, paired with an input that describes a SQL table.  Write a SQL query that ret

Set up the details for the model.

In [5]:
from peft import LoraConfig, get_peft_model
import transformers
import datasets

LORA_R = 4
LORA_ALPHA = 16
LORA_DROPOUT = .1
CUTOFF_LEN = 256
BATCH = 128
MICRO_BATCH = 4
N_GAS = BATCH//MICRO_BATCH
EPOCHS = 1
LR = 1e-5

lora_cfg = LoraConfig(
    r = LORA_R,
    lora_alpha=LORA_ALPHA,
    lora_dropout=LORA_DROPOUT,
    task_type='CASUAL_LM',
    target_modules=['q_proj','v_proj']
)

model = get_peft_model(model,lora_cfg)

tokenizer.pad_token_id = 0

d = {'prompt': data_txt}

data = datasets.Dataset.from_dict(d)
data = data.map(lambda x:
        tokenizer(
        x['prompt'],
        truncation=True,
        max_length=CUTOFF_LEN,
        padding="max_length"
        ))

data = data.remove_columns('prompt')

targs = transformers.TrainingArguments(
    per_device_train_batch_size=MICRO_BATCH,
    gradient_accumulation_steps=N_GAS,
    warmup_steps=0,
    num_train_epochs=EPOCHS,
    learning_rate=LR,
    fp16=True,
    logging_steps=1,
    output_dir='sqllama-out',
    save_total_limit=3,
    remove_unused_columns=False
)


model.config.use_cache = False

Map:   0%|          | 0/56355 [00:00<?, ? examples/s]

ignore - just trying to figure out huggingface datasets

In [6]:
print(data)
print(data[0])

#from datasets import load_dataset


#!git clone https://github.com/tloen/alpaca-lora.git
#dalp = load_dataset("json", data_files="alpaca-lora/alpaca_data.json")
#print(dalp)

#dalp = dalp.map(lambda x : {'blah':'blah'})
#print(dalp)

Dataset({
    features: ['input_ids', 'attention_mask'],
    num_rows: 56355
})
{'input_ids': [0, 13866, 338, 263, 1139, 393, 16612, 263, 848, 2009, 29892, 3300, 2859, 411, 385, 1881, 393, 16612, 263, 3758, 1591, 29889, 29871, 14350, 263, 3758, 2346, 393, 5663, 17180, 278, 848, 29889, 13, 2277, 29937, 894, 29901, 24948, 592, 825, 278, 11486, 526, 363, 4275, 8314, 29871, 13, 2277, 29937, 10567, 29901, 6137, 29871, 29896, 29899, 29896, 29900, 29900, 29900, 29896, 29947, 29896, 29899, 29896, 756, 4341, 4306, 29914, 357, 768, 706, 313, 726, 511, 1626, 29914, 7042, 12384, 313, 726, 511, 5809, 313, 726, 511, 7583, 269, 1188, 273, 313, 726, 511, 7583, 3652, 313, 726, 511, 3664, 267, 313, 726, 467, 259, 13, 2277, 29937, 673, 29901, 5097, 29871, 8695, 3895, 29871, 29896, 29899, 29896, 29900, 29900, 29900, 29896, 29947, 29896, 29899, 29896, 5754, 9626, 269, 1188, 273, 353, 525, 6156, 2692, 29950, 319, 29965, 10810, 1964, 10764, 29915, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0

In [6]:


trainer = transformers.Trainer(
    model = model,
    train_dataset = data,
    args = targs,
    data_collator=transformers.DataCollatorForLanguageModeling(tokenizer, mlm=False)
)
trainer.train(resume_from_checkpoint=False)
model.save_pretrained('sqllama-out')

In [7]:
def get_query(q):
    
    toks = tokenizer(q , return_tensors='pt')
    ctoks = toks.input_ids.to('cuda')
    gen = model.generate(ctoks, max_length=256)
    return tokenizer.decode(gen[0])

M = len(nl_q)
j = random.randint(0,M-1)
qs = nl_q[j] + '\n### Answer: '
a = sql_a[j]

ma = get_query(qs)

#print(qs)
print('from model')
print(ma)
print('expected answer')
print(a)


/home/matt/hf/sqllama-V0/.venv/lib/python3.7/site-packages/transformers/generation/utils.py:1220: UserWarning: You have modified the pretrained model configuration to control generation. This is a deprecated strategy to control generation and will be removed soon, in a future version. Please use a generation configuration file (see https://huggingface.co/docs/transformers/main_classes/text_generation)
  "You have modified the pretrained model configuration to control generation. This is a"
/home/matt/hf/sqllama-V0/.venv/lib/python3.7/site-packages/torch/utils/checkpoint.py:31: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn("None of the inputs have requires_grad=True. Gradients will be None")


Below is a question that describes a data request, paired with an input that describes a SQL table.  Write a SQL query that retrieves the data.
### Question: What county has a CERCLIS ID of scd037405362?
### Input: Table 2-11960788-1 has columns CERCLIS ID (text),Name (text),County (text),Proposed (text),Listed (text).  
### Answer: 
<unk>Below is a question that describes a data request, paired with an input that describes a SQL table.  Write a SQL query that retrieves the data.
### Question: What county has a CERCLIS ID of scd037405362?
### Input: Table 2-11960788-1 has columns CERCLIS ID (text),Name (text),County (text),Proposed (text),Listed (text).  
### Answer:  SELECT County FROM 2-11960788-1 WHERE CERCLIS ID = 'scd037405362'  
### Question: What county has a CERCLIS ID of scd037405362?
### Input: Table 2-11960788-1 has columns CERCLIS ID (text),Name (text),County (text),Proposed (text),Listed (text).  
### Answer:  SELECT County FROM 2-11960788-1 WHERE CERCLIS ID

### Answer: S